Grafico del mapa de Chile

In [ ]:
import pandas as pd
url="R_results\Diferencia_mapa_2017.csv"
df=pd.read_csv(url)
print(df.head(5))
print(df.shape)

In [ ]:
print(df['Diferencia_Hombres_Mujeres'].dtype)

print(df.dtypes)

In [6]:
# Replace comma with a decimal point
df['Latitud'] = df['Latitud'].str.replace(',', '.')
df['Longitud'] = df['Longitud'].str.replace(',', '.')
df['Diferencia_Hombres_Mujeres'] = df['Diferencia_Hombres_Mujeres'].str.replace(',', '.').astype(float)

In [7]:
# Convert to float
df['Diferencia_Hombres_Mujeres'] = df['Diferencia_Hombres_Mujeres'].astype(float)
df['Latitud'] = df['Latitud'].astype(float)
df['Longitud'] = df['Longitud'].astype(float)

print(df.dtypes)

Año                             int64
Región                         object
Diferencia_Hombres_Mujeres    float64
Abreviatura                    object
Latitud                       float64
Longitud                      float64
dtype: object


Crearemos una solicitud (query) de los datos a graficar para el año 2020 y la guardaremos en una variable df_2020

In [8]:
import plotly.express as px

df_2020 = df.query('Año == 2020')

Crear grafica interactiva con Plotly del Año 2020

In [9]:
import plotly.express as px

fig = px.bar(df_2020, x='Abreviatura', y='Diferencia_Hombres_Mujeres')
fig.show()

Para graficar un mapa de Chile con "Choropleth" necesitamos transmutar df_2020 a una tabla de datos con cada Región como fila para ser usado segun los parametros documentados.
https://plotly.github.io/plotly.py-docs/generated/plotly.express.choropleth.html

In [10]:
print(df_2020.dtypes)

Año                             int64
Región                         object
Diferencia_Hombres_Mujeres    float64
Abreviatura                    object
Latitud                       float64
Longitud                      float64
dtype: object


Cambiar el index por Región, para ordenar los datos por cada Región.

In [11]:
df_2020_pivot = df_2020.set_index("Región")[["Abreviatura", "Diferencia_Hombres_Mujeres", "Latitud", "Longitud"]].reset_index()

In [31]:
# Rename the 'Región' column to 'Region' to match the GeoJSON file
df_2020_pivot = df_2020_pivot.rename(columns={'Región': 'Region'})

Crearemos un gráfico con el mapa de Chile, representando las variables de la columna "Diferencia_Hombres_Mujeres" con una escala de colores. 

In [34]:
import pandas as pd
import requests
import plotly.express as px

# Read the GeoJSON file
url = 'https://raw.githubusercontent.com/caracena/chile-geojson/master/regiones.json'
# Request the map data
chile_geojson = requests.get(url).json()


# Create the choropleth map
fig = px.choropleth(
    data_frame=df_2020_pivot,
    geojson=chile_geojson,
    locations='Region',
    featureidkey='properties.Region',
    color='Diferencia_Hombres_Mujeres',
    color_continuous_scale='amp',
    labels={'Diferencia_Hombres_Mujeres': 'Diferencia de Tasas de Ocupación (pp)'},
    hover_data={'Region': False, 'Diferencia_Hombres_Mujeres': ':.2f'}
)

# Update the map layout
fig.update_geos(
    showcountries=True,
    showcoastlines=True,
    showland=True,
    fitbounds="locations",
    projection_type='mercator'
)
fig.update_layout(
    title_text='Diferencia de Ocupación de Chile (pp)',
    font=dict(
        family='Ubuntu',
        size=18,
        color='#7f7f7f'
    ),
    annotations=[dict(
        x=0.55,
        y=-0.1,
        xref='paper',
        yref='paper',
        text='Fuente: <a href="https://bancodatosene.ine.cl/">Banco estadístico del INE</a>',
        showarrow=False
    )],
    coloraxis_colorbar=dict(
        title='Diferencia de Ocupación (pp)'
    ),
    width=900,  # adjust the width as needed
    height=700, # adjust the height as needed
    margin=dict(l=50, r=50, b=50, t=100, pad=4)
)

# Show the map
fig.show()


We have some missing values, surelly because the names from the GeoJSON data and the INE data have not the same names for the Region column
we will call the names of the json file, because we can se the INE names in the df_2020_pivot file (only 16 rows)

In [17]:
import json
# Open the file
with open('Geojason/regiones.json', 'r') as f:
    data = json.load(f)

region_names = []
for feature in data['features']:
    region_names.append(feature['properties']['Region'])
    
print(region_names)


['RegiÃ³n de Arica y Parinacota', 'RegiÃ³n de TarapacÃ¡', 'RegiÃ³n de Antofagasta', 'RegiÃ³n de Magallanes y AntÃ¡rtica Chilena', 'RegiÃ³n de AysÃ©n del Gral.IbaÃ±ez del Campo', 'RegiÃ³n de Atacama', 'RegiÃ³n de Coquimbo', 'RegiÃ³n de ValparaÃ\xadso', 'RegiÃ³n Metropolitana de Santiago', 'RegiÃ³n de Los Lagos', 'RegiÃ³n de Los RÃ\xados', 'RegiÃ³n de La AraucanÃ\xada', 'RegiÃ³n del BÃ\xado-BÃ\xado', 'RegiÃ³n de Ã‘uble', 'RegiÃ³n del Maule', "RegiÃ³n del Libertador Bernardo O'Higgins"]


In [18]:
print(df_2020_pivot['Region'].unique())


['Región Metropolitana de Santiago' 'Región de Antofagasta'
 'Región de Arica y Parinacota' 'Región de Atacama'
 'Región de Aysén del Gral. Carlos Ibáñez del Campo' 'Región de Coquimbo'
 'Región de La Araucanía' 'Región de Los Lagos' 'Región de Los Ríos'
 'Región de Magallanes y La Antártica Chilena' 'Región de Tarapacá'
 'Región de Valparaíso' 'Región de Ñuble' 'Región del Biobío'
 "Región del Libertador Gral. Bernardo O'Higgins" 'Región del Maule'
 'Total país']


RegiÃ³n de Magallanes y AntÃ¡rtica Chilena | Región de Magallanes y La Antártica Chilena
RegiÃ³n de AysÃ©n del Gral.IbaÃ±ez del Campo | Región de Aysén del Gral. Carlos Ibáñez del Campo
RegiÃ³n del BÃ\xado-BÃ\xado | Región del Biobío
RegiÃ³n del Libertador Bernardo O'Higgins | Región del Libertador Gral. Bernardo O'Higgins

We can se that the problem is that the names used for the data in the GeoJSON repository are not the same that the INE use in their tables.
We could modify either, but because we already did a request of the repository data, we will change this for values in the chile_geojson variable.

In [19]:
# We will use a not elegant, but simple for loop, because we don't know if the accents inputs will be readed as the previous code or as a spanish text.
for feature in chile_geojson['features']:
    # Get the current value of the Region key
    current_region = feature['properties']['Region']
    
    # Update the value of the Region key if it matches one of the desired values
    if current_region == "Región de Magallanes y Antártica Chilena":
        feature['properties']['Region'] = "Región de Magallanes y La Antártica Chilena"
    elif current_region == "Región de Aysén del Gral.Ibañez del Campo":
        feature['properties']['Region'] = "Región de Aysén del Gral. Carlos Ibáñez del Campo"
    elif current_region == "Región del Bío-Bío":
        feature['properties']['Region'] = "Región del Biobío"
    elif current_region == "Región del Libertador Bernardo O'Higgins":
        feature['properties']['Region'] = "Región del Libertador Gral. Bernardo O'Higgins"

# Check the Region values in the GeoJSON file
for feature in chile_geojson['features']:
    print(feature['properties']['Region'])



Región de Arica y Parinacota
Región de Tarapacá
Región de Antofagasta
Región de Magallanes y La Antártica Chilena
Región de Aysén del Gral. Carlos Ibáñez del Campo
Región de Atacama
Región de Coquimbo
Región de Valparaíso
Región Metropolitana de Santiago
Región de Los Lagos
Región de Los Ríos
Región de La Araucanía
Región del Biobío
Región de Ñuble
Región del Maule
Región del Libertador Gral. Bernardo O'Higgins


Ahora que estamos seguros que todos los valores coinciden en el archivo JSON y en nuestra base de datos, podemos volver a graficar y agregar nuestras modificaciones.

In [21]:
# Create the choropleth map
fig = px.choropleth(
    data_frame=df_2020_pivot,
    geojson=chile_geojson,
    locations='Region',
    featureidkey='properties.Region',
    color='Diferencia_Hombres_Mujeres',
    color_continuous_scale='Hot_r',
    range_color=[10, 30],  # set the color scale range
    labels={'Diferencia_Hombres_Mujeres': 'pp'},
    hover_data={'Region': True, 'Diferencia_Hombres_Mujeres': ':.2f'}
)

# Change the map layout
fig.update_geos(
    showcountries=False,
    showcoastlines=True,
    showland=False,
    visible=False,  # Elimina el marco
    projection_type='mercator',
# Chile = latitud -35.675147 y longitud -71.542969.
    center=dict(lat=-33.5, lon=-70.5), 
    fitbounds='geojson'
)

# Change the graph layout
fig.update_layout(
    title={
        'text': 'Diferencia en Regiones<br><sub>Resultado en puntos porcentuales</sub><sub> (Período 2020)</sub>',
        'font': {'family': 'Ubuntu', 'size': 24, 'color': 'black'},
        'x': 0.2, # set the x position of the tittle
        'y': 0.9 # set the y position of the tittle
    },
    annotations=[dict(
        x=0.2,
        y=-0,
        xref='paper',
        yref='paper',
        text='Fuente: <a href="https://bancodatosene.ine.cl/">Banco estadístico del INE</a>',
        showarrow=False
    )],
    coloraxis_colorbar=dict(
        title='p.p.',
        lenmode='pixels',
        len=400,
        thicknessmode='pixels',
        thickness=15,
        x=0.2,  # adjust the position of the color bar along the x-axis
        xanchor='left',  # anchor the color bar to the left side of the plot
        yanchor='middle', # anchor the color bar to the middle side of the plot
        y=0.45, # adjust the position of the color bar along the y-axis
    ),
    width=850,  # adjust the width as needed
    height=800, # adjust the height as needed
    margin=dict(l=0, r=10, t=0, pad=10), # adjust the borders
)

# Change the traces layout
fig.update_traces(
    hovertemplate='<b>%{location}</b><br>' +
                  'p.p. = %{z:.2f}<br>' +
                  '<extra></extra>'
)
# Show the map
fig.show()

## NOW THE HARD PART

Because we want to create a single visual on how the Opancy by gender has changed over the year for every Region. We will use this map as a reference to create a display option, wich will contain the years (Año columns).

First we need to make the same corrections to the df loaded data: Change the Región name column to 'Region' and Transmute the table.

In [23]:
# Rename the "Región" column to "Region"
df = df.rename(columns={'Región': 'Region'})

We already changed the values in the GeoJSON data set to match with the ones entered in the df variable.
So we will continue with the ploting.

In [22]:
# We import Dash, pandas, json and plotly
from dash import Dash, dcc, html, Input, Output
import pandas as pd
import json
import plotly.express as px

The GeoJson file is already loaded and modified to match the values in the chile_geojson variable.
Documentación: https://plotly.com/python/choropleth-maps/